In [73]:
import requests
from bs4 import BeautifulSoup
from textblob import TextBlob
import re
import warnings
warnings.filterwarnings('ignore', message='A NumPy version.*"')

base_url = 'https://www.yelp.com/biz/'
url = "https://www.yelp.com/biz/ryptic-room-escape-san-mateo-3"
html = requests.get(url)
soup = BeautifulSoup(html.text, 'html.parser')

In [130]:
html_otc = requests.get('https://www.yelp.com/biz/off-the-couch-fremont')
soup_otc = BeautifulSoup(html_otc.text, 'html.parser')
print(soup_otc.prettify())

<!DOCTYPE html>
<html lang="en-US" prefix="og: http://ogp.me/ns#" style="margin: 0;padding: 0; border: 0; font-size: 100%; font: inherit; vertical-align: baseline;">
 <head>
  <script>
   document.documentElement.className=document.documentElement.className.replace(no-j/,"js");
  </script>
  <meta content="text/html; charset=utf-8" http-equiv="Content-Type"/>
  <meta content="en-US" http-equiv="Content-Language"/>
  <meta content="width=device-width, initial-scale=1, shrink-to-fit=no" name="viewport"/>
  <link content="#FF1A1A" href="https://s3-media0.fl.yelpcdn.com/assets/srv0/yelp_large_assets/b2bb2fb0ec9c/assets/img/logos/yelp_burst.svg" rel="mask-icon" sizes="any"/>
  <link href="https://s3-media0.fl.yelpcdn.com/assets/srv0/yelp_large_assets/dcfe403147fc/assets/img/logos/favicon.ico" rel="shortcut icon"/>
  <script>
   window.ga=window.ga||function(){(ga.q=ga.q||[]).push(arguments)};ga.l=+new Date;window.ygaPageStartTime=new Date().getTime();
  </script>
  <script>
   window.yelp =

In [74]:
print(soup.prettify())

<!DOCTYPE html>
<html lang="en-US" prefix="og: http://ogp.me/ns#" style="margin: 0;padding: 0; border: 0; font-size: 100%; font: inherit; vertical-align: baseline;">
 <head>
  <script>
   document.documentElement.className=document.documentElement.className.replace(no-j/,"js");
  </script>
  <meta content="text/html; charset=utf-8" http-equiv="Content-Type"/>
  <meta content="en-US" http-equiv="Content-Language"/>
  <meta content="width=device-width, initial-scale=1, shrink-to-fit=no" name="viewport"/>
  <link content="#FF1A1A" href="https://s3-media0.fl.yelpcdn.com/assets/srv0/yelp_large_assets/b2bb2fb0ec9c/assets/img/logos/yelp_burst.svg" rel="mask-icon" sizes="any"/>
  <link href="https://s3-media0.fl.yelpcdn.com/assets/srv0/yelp_large_assets/dcfe403147fc/assets/img/logos/favicon.ico" rel="shortcut icon"/>
  <script>
   window.ga=window.ga||function(){(ga.q=ga.q||[]).push(arguments)};ga.l=+new Date;window.ygaPageStartTime=new Date().getTime();
  </script>
  <script>
   window.yelp =

In [ ]:
# Returns the upper bound for looping through the review pages.
# Example: If the review page consists of 20 pages, then the search query will
# append '?start=190' to the URL to get to the last review page. This function will
# return 191, the upper bound needed for a for-loop to go through all the review pages.
def get_reviews_loop_upper_bound(soup_obj):
    upper_bound = 0
    # 'css-chan6m' elements contain a "# of #", with the former being the current review page
    # and the latter being the last review page.
    chan6m_elems = soup_obj.find_all(class_='css-chan6m')
    for chan6m_elem in chan6m_elems:
        if 'of' in chan6m_elem.text:
            upper_bound = (int(chan6m_elem.text.split()[-1]) - 1) * 10 + 1 # get last review page
            return upper_bound
    return upper_bound

get_reviews_loop_upper_bound(soup)

In [107]:
# Takes in a soup object and retuns the escape room's name and the city the room is in
def get_room_info(soup_obj):
    room_title_info = soup_obj.title.text.split('-')
    
    # Title is the 0th element in the list with trailing white spaces
    room_name = room_title_info[0].strip().lower()

    # Address is the 2nd elemnt in the list, city is the second to last element in list with trailing white spaces
    room_city = room_title_info[2].split(',')[-2].strip()

    # Get the overall rating of the escape room
    overall_rating_pattern = re.compile(r'(?:[1-4](?:\.5)?|5(?:\.0)?) star rating')
    # seems like 2 of the same gets extracted, pick the 0th element
    room_overall_element = soup_obj.find_all('div', {'aria-label': overall_rating_pattern, 'class': 'css-1v6kfrx'})[0]
    room_overall_rating = float(room_overall_element['aria-label'].split()[0])

    return room_name, room_city, room_overall_rating

room_name, room_city, room_overall_rating = get_room_info(soup)
room_name, room_city, room_overall_rating


('ryptic room escape', 'San Mateo', 4.5)

## get all page reviews and ratings

Yelp is pretty clever. For each page_rating get, we want to only get the first 10, since yelp also offers 10 "people also viewed". BS4 will also capture those ratings and will be the latter 10 ratings. (number of ratings and reviews is always double)


In [129]:
base_url = 'https://www.yelp.com/biz/'
room_url = 'off-the-couch-fremont'
upper_bound = 171

# Gets every review of an escape room and returns it in a list
def get_all_page_reviews_and_ratings(base_url, room_url, upper_bound):

    # Helper function that takes in a soup object and returns the reviews of
    # that "page" as a list of reviews
    def get_page_reviews(soup_obj):
        page_reviews = []
        # Class='raw__09f24__T4Ezm' and lang='en' tags specifies reviews
        review_elements = soup_obj.find_all(class_='raw__09f24__T4Ezm', lang='en')
        for review_element in review_elements:
            review = review_element.text
            page_reviews.append(review)
        return page_reviews
    
    # Helper function that takes in a soup object and returns the rating of
    # that "page" as a list of ratings
    def get_page_ratings(soup_obj):        
        # regex pattern to capture review ratings
        user_rating_pattern = re.compile(r'(?:[1-4](?:\.5)?|5(?:\.0)?) star rating')
        page_ratings = []
        rating_elements = soup_obj.find_all('div', {'aria-label': user_rating_pattern, 'class': 'css-14g69b3'})
        for rating_element in rating_elements:
            rating_value = rating_element['aria-label'].split()[0] # just want the number
            page_ratings.append(rating_value)

        # list comp to convert strings to ints (user ratings have no decimals)
        return page_ratings
        #return [int(page_rating) for page_rating in page_ratings[:-10]]

    ### FUNCTION BEGIN ###
    all_reviews = []
    all_ratings = []
    for i in range(0, upper_bound, 10): # loop through all review pages
        print(f'appending reviews for page {int(i/10) + 1}...')
        full_url = base_url + room_url
        if i != 0: # append appropriate search query for review page
            full_url += f'?start={i}' 
        
        # Make html request on full_url and create soup object
        html = requests.get(full_url)
        soup_obj = BeautifulSoup(html.text, 'html.parser')

        # .extend instead of .append because get_page_reviews returns a list
        all_reviews.extend(get_page_reviews(soup_obj))
        print(f'length of reviews: {len(all_reviews)}')

        # repeat for ratings
        all_ratings.extend(get_page_ratings(soup_obj))
        print(f'length of ratings: {len(all_ratings)}')

    return all_reviews, all_ratings

test_reviews, test_ratings = get_all_page_reviews_and_ratings(base_url, room_url, 21) 

appending reviews for page 1...
length of reviews: 10
length of ratings: 22
appending reviews for page 2...
length of reviews: 20
length of ratings: 44
appending reviews for page 3...
length of reviews: 31
length of ratings: 68


In [128]:
len(test_ratings), len(test_reviews)

(37, 31)

In [126]:
test_ratings

[3,
 5,
 5,
 5,
 5,
 5,
 5,
 5,
 5,
 5,
 5,
 5,
 3,
 5,
 5,
 5,
 5,
 5,
 5,
 5,
 5,
 5,
 5,
 5,
 3,
 5,
 5,
 5,
 5,
 5,
 5,
 5,
 5,
 5,
 1,
 5,
 5]

In [127]:
test_reviews

['Extremely fun and innovative escape room. Highly recommend if you are looking for something to do in Fremont!',
 'My girlfriend and I love this escape room series so far. I would say the three things that we enjoy the most about it are:1) The storyline2) The puzzles3) The hospitality The best part of all of it is that it\'s an "at your pace" type of experience, which allows you to go as fast or as slow as you want to! Beyond the puzzles and interactive elements, the music, noises, and light effects are all entertaining and keep you on your toes!10/10 recommend this escape room series to anyone and will continue to give reviews after each experience! We finished Occam\'s Apartment and started on Norcross Art Gallery tonight!',
 'I\'ve never made a review for anything on Yelp until now. I felt that I had to for Off the Couch Games due to the amazing experience we had. We played Chapter 1: Occam\'s Apartment and we were immediately intrigued with the story that was set up. Many escape r

In [105]:
# Takes in a list of reviews and returns a list of tuples with the 
# 0th element being the sentiment score and the 1st element being the
# corresponding review.
def compute_sentiments(reviews, decimals=4):
    sentiment_scores = []
    for review in reviews:
        review_blob = TextBlob(review)
        sentiment_score = review_blob.sentiment.polarity
        sentiment_scores.append((round(sentiment_score, decimals)))
    return sentiment_scores

test_sentiment_scores = compute_sentiments(test_reviews)
test_sentiment_scores

[0.275, -0.0701, 0.2479, 0.3514, 0.2719, 0.3086, 0.1455, 0.532, 0.3409, 0.0928]

In [ ]:
### TESTING MYSQL CONNECTION ###

import mysql.connector
import configparser

# Read configuration from config.ini
config = configparser.ConfigParser()
config.read('config.ini')

# Retrieve database settings from the configuration
host = config['mysql']['host']
user = config['mysql']['user']
password = config['mysql']['password']
database = config['mysql']['database']


# Establish a connection to the MySQL database
cnx = mysql.connector.connect(
    host=host,
    user=user,
    password=password,
    database=database
)

cursor = cnx.cursor()

sql_query = ("SELECT * FROM customers")

cursor.execute(sql_query)

for (id, first_name, last_name, email) in cursor:
  print(f'{id}, {first_name}, {last_name}, {email}')
cursor.close()
cnx.close()


In [ ]:
a = [(1, 2, 3), (4, 5, 6)]
